In [4]:
import pandas as pd 
import numpy as np 
import nltk
import os
import sklearn
import parquet

In [7]:
data1 = pd.read_parquet("news-00000-of-00007-0ff1ec222cd690f2.parquet")
data2 = pd.read_parquet("news-00001-of-00007-7c273f5de9017dc5.parquet")
data3 = pd.read_parquet("telegram_blogs-00000-of-00001-80087cf60adbe6d4.parquet")

In [21]:
# Extract the 'text' column from each DataFrame
texts1 = data1['text']
texts2 = data2['text']
texts3 = data3['text']

# Concatenate the 'text' columns from all three DataFrames
all_texts = pd.concat([texts1, texts2, texts3], ignore_index=True)
data = pd.DataFrame(all_texts, columns=['text'])


In [22]:
# Calculate the length of each text entry
text_lengths = data['text'].str.len()

# Display the distribution of text lengths
length_distribution = text_lengths.describe()

# Print the distribution
print(length_distribution)


count    643523.000000
mean       1225.167071
std        2613.174490
min           0.000000
25%         271.000000
50%         689.000000
75%        1362.000000
max      299171.000000
Name: text, dtype: float64


In [19]:
import random
import string

def random_letter():
    """Returns a random alphanumeric character."""
    return random.choice(string.ascii_letters + string.digits)

def replace_random_letters(word, pct=0.15):
    """Replaces random letters in a word with a given probability."""
    if random.random() < pct:
        char_pos = random.choice(range(len(word)))
        return word[:char_pos] + random_letter() + word[char_pos + 1:]
    else:
        return word

def misspell_text(text, pct=0.15, last_letter_error_pct=0.20):
    """Generates a misspelled version of the input text."""
    words = text.split()
    misspelled_words = [replace_random_letters(word, pct) for word in words]
    
    # Apply last letter error with a different probability
    for i, word in enumerate(misspelled_words):
        if random.random() < last_letter_error_pct:
            if len(word) > 1:  # Ensure word has more than 1 character
                misspelled_words[i] = word[:-1] + random_letter()
    
    return ' '.join(misspelled_words)


In [23]:
data.rename(columns={'text':'ground_truth'}, inplace=True)


In [24]:
data

AttributeError: 'Index' object has no attribute '_format_flat'

                                             ground_truth
0       «Toshshahartransxizmat» AJ Axborot xizmati jam...
1       Oʻzbekiston Respublikasi Prezidenti Shavkat Mi...
2       Oʻzbekistonning AQSHdagi elchisi Javlon Vahobo...
3       Oliy Majlisning Inson huquqlari boʻyicha vakil...
4       Bu haqda Agentlik axborot xizmati xabar berdi....
...                                                   ...
643518  Марказий Осиё давлатлари бўйлаб эркин ҳаракатл...
643519  ​​Олий таълим муассасаларида \nКоррупцияга қар...
643520  ​​Қирғизистонда вазир лавозимига тайинланганид...
643521  Исроил ва Фаластин ўқ отишни тўхтатишди. "Масж...
643522  ​​АҚШ 20 та давлатга ҳарбий иншоотлар учун 240...

[643523 rows x 1 columns]

In [25]:
# Apply the function to create misspelled texts
data['sample_misspelled'] = data['ground_truth'].apply(lambda x: misspell_text(x))

In [31]:
print(data)

                                             ground_truth  \
0       «Toshshahartransxizmat» AJ Axborot xizmati jam...   
1       Oʻzbekiston Respublikasi Prezidenti Shavkat Mi...   
2       Oʻzbekistonning AQSHdagi elchisi Javlon Vahobo...   
3       Oliy Majlisning Inson huquqlari boʻyicha vakil...   
4       Bu haqda Agentlik axborot xizmati xabar berdi....   
...                                                   ...   
643518  Марказий Осиё давлатлари бўйлаб эркин ҳаракатл...   
643519  ​​Олий таълим муассасаларида \nКоррупцияга қар...   
643520  ​​Қирғизистонда вазир лавозимига тайинланганид...   
643521  Исроил ва Фаластин ўқ отишни тўхтатишди. "Масж...   
643522  ​​АҚШ 20 та давлатга ҳарбий иншоотлар учун 240...   

                                        sample_misspelled  
0       «Toshshahartransxizmat» A6 Axborot xizmatG jam...  
1       Oʻzbekiston Respublikasi Prezidenti Shavkat Mi...  
2       Oʻzbekistonnin6 AQSHdagi elchisi Javlog Vahobo...  
3       Oliy Majlisning Ins

In [32]:
expanded_data = pd.concat([data['ground_truth'], data['ground_truth']], ignore_index=True).to_frame(name='ground_truth')


In [33]:
import random

def creative_misspell(text):
    """Apply creative misspelling strategies to the text."""
    words = text.split()
    misspelled_words = []
    for word in words:
        # Example of a simple typographical error
        if random.random() < 0.05:  # Apply with 5% probability
            word = word.replace('the', 'teh')
        
        # Example of omitting letters
        if random.random() < 0.05 and len(word) > 3:
            omit_index = random.randint(1, len(word) - 2)  # Avoid first and last character
            word = word[:omit_index] + word[omit_index + 1:]
        
        # Add more rules as needed
        
        misspelled_words.append(word)
    
    return ' '.join(misspelled_words)


In [34]:
expanded_data['sample_misspelled'] = expanded_data['ground_truth'].apply(creative_misspell)
